
## Overview:

In this notebook, we embark on an ETL (Extract, Transform, Load) process aimed at refining raw data into a polished format[bronze - silver] and [silver - gold], ready for consumption in Power BI dashboards.

Our primary focus lies on two distinct datasets: `userdata` and `devicedata`.

1. **`userdata` Dataset:**
   This dataset provides essential information about users' health and lifestyle. It includes fields such as `userid`, `gender`, `age`, `height`, `weight`, `smoker`, `familyhistory`, `cholestlevs`, `bp`, and `risk`. These attributes capture vital health indicators and demographics necessary for comprehensive analysis.

2. **`devicedata` Dataset:**
   The `devicedata` dataset complements the user-centric data with insights derived from IoT devices. It includes metrics like `calories_burnt`, `miles_walked`, `num_steps`, and `timestamp`. Additionally, it contains device-specific information such as `device_id` and `user_id`, facilitating correlation between user activity and device usage.

## ETL Process Overview:
- **Extract:** Retrieve raw data from the provided Databricks sample datasets, preparing it for transformation.
- **Transform:**
  - **Cleansing:** Handle missing or inconsistent data.
  - **Aggregating:** Aggregate data at the hourly level, breaking down timestamp into date and time.
  - **Enriching:** Enhance data quality and utility.
- **Load:** Load the transformed data into a Delta Lake tables optimized for efficient querying and visualization.

## Aggregation at Hourly Level:
We will aggregate the data to an hourly granularity, allowing for more efficient analysis and visualization. This aggregation will enable us to observe trends and patterns in user activity and health metrics over time, providing valuable insights for decision-making.

## Goals:
- Achieve data consistency and integrity across both datasets.
- Enhance data quality through cleaning and normalization procedures.
- Aggregate data at the hourly level for improved analysis granularity.
- Optimize data structures for efficient querying and visualization in Power BI.

By following this journey, we aim to unlock the full potential of Databricks' IoT datasets, empowering data-driven decision-making and actionable insights in health and wellness analysis. Let's dive in and refine this raw data into a valuable asset for Power BI dashboards!

# Data Extraction from Databricks Datasets

## Extraction from `dbfs:/databricks-datasets/iot-stream/data-device/`

### Brief Info about `%fs ls dbfs:/databricks-datasets/iot-stream/data-device/`:

- The `%fs ls` command is used to list files and directories in Databricks File System (DBFS).
- `dbfs:/databricks-datasets/iot-stream/data-device/` is the directory path from which we are extracting data.
- This directory likely contains raw data files related to IoT devices, which we will extract for further processing.
- The data files may include metrics such as device IDs, user IDs, timestamps, and various sensor readings.

## Extraction Process:

1. Use the `%fs ls` command to list files and directories in `dbfs:/databricks-datasets/iot-stream/data-device/`.
2. Identify the relevant data files needed for our analysis.
3. Extract the selected data files for further processing and analysis.

The extraction step is crucial as it forms the foundation for subsequent data transformation and loading processes. By accurately extracting the required data, we ensure that our analysis is based on reliable and relevant information.


In [ ]:
%fs ls dbfs:/databricks-datasets/iot-stream/data-device/

path name size modificationTime dbfs:/databricks-datasets/iot-stream/data-device/part-00000.json.gz part-00000.json.gz 2610922 1532465738000 dbfs:/databricks-datasets/iot-stream/data-device/part-00001.json.gz part-00001.json.gz 2612478 1532465738000 dbfs:/databricks-datasets/iot-stream/data-device/part-00002.json.gz part-00002.json.gz 2619023 1532465738000 dbfs:/databricks-datasets/iot-stream/data-device/part-00003.json.gz part-00003.json.gz 2620016 1532465738000 dbfs:/databricks-datasets/iot-stream/data-device/part-00004.json.gz part-00004.json.gz 2618699 1532465738000 dbfs:/databricks-datasets/iot-stream/data-device/part-00005.json.gz part-00005.json.gz 2619772 1532465738000 dbfs:/databricks-datasets/iot-stream/data-device/part-00006.json.gz part-00006.json.gz 2619027 1532465738000 dbfs:/databricks-datasets/iot-stream/data-device/part-00007.json.gz part-00007.json.gz 2619832 1532465738000 dbfs:/databricks-datasets/iot-stream/data-device/part-00008.json.gz part-00008.json.gz 2617893 1532465738000 dbfs:/databricks-datasets/iot-stream/data-device/part-00009.json.gz part-00009.json.gz 2619764 1532465738000 dbfs:/databricks-datasets/iot-stream/data-device/part-00010.json.gz part-00010.json.gz 2620205 1532465766000 dbfs:/databricks-datasets/iot-stream/data-device/part-00011.json.gz part-00011.json.gz 2619880 1532465768000 dbfs:/databricks-datasets/iot-stream/data-device/part-00012.json.gz part-00012.json.gz 2619155 1532465771000 dbfs:/databricks-datasets/iot-stream/data-device/part-00013.json.gz part-00013.json.gz 2618436 1532465772000 dbfs:/databricks-datasets/iot-stream/data-device/part-00014.json.gz part-00014.json.gz 2619029 1532465773000 dbfs:/databricks-datasets/iot-stream/data-device/part-00015.json.gz part-00015.json.gz 2619296 1532465775000 dbfs:/databricks-datasets/iot-stream/data-device/part-00016.json.gz part-00016.json.gz 2619911 1532465776000 dbfs:/databricks-datasets/iot-stream/data-device/part-00017.json.gz part-00017.json.gz 2619952 1532465776000 dbfs:/databricks-datasets/iot-stream/data-device/part-00018.json.gz part-00018.json.gz 2619592 1532465789000 dbfs:/databricks-datasets/iot-stream/data-device/part-00019.json.gz part-00019.json.gz 2620210 1532465781000

In [ ]:
deviceData_raw = spark.read.json("dbfs:/databricks-datasets/iot-stream/data-device")

In [ ]:
deviceData_raw.printSchema()

root
 |-- calories_burnt: double (nullable = true)
 |-- device_id: long (nullable = true)
 |-- id: long (nullable = true)
 |-- miles_walked: double (nullable = true)
 |-- num_steps: long (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- user_id: long (nullable = true)
 |-- value: string (nullable = true)



In [ ]:
deviceData_raw.show()

+--------------+---------+------+------------+---------+--------------------+-------+--------------------+
|calories_burnt|device_id|    id|miles_walked|num_steps|           timestamp|user_id|               value|
+--------------+---------+------+------------+---------+--------------------+-------+--------------------+
|         250.7|        5|950000|       2.507|     5014|2018-07-22 06:44:...|     24|{"user_id": 24, "...|
|         126.8|       13|950001|       1.268|     2536|2018-07-21 01:18:...|     24|{"user_id": 24, "...|
|         365.7|        5|950002|       3.657|     7314|2018-07-24 12:42:...|      4|{"user_id": 4, "c...|
|         489.8|       10|950003|       4.898|     9796|2018-07-23 22:56:...|     22|{"user_id": 22, "...|
|        280.15|       13|950004|      2.8015|     5603|2018-07-21 13:50:...|     34|{"user_id": 34, "...|
|         591.6|        1|950005|       5.916|    11832|2018-07-23 11:05:...|     21|{"user_id": 21, "...|
|         548.1|       12|950006|    

In [ ]:
deviceData_raw.select('value').show(truncate=False)

+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
|value                                                                                                                                                                    |
+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
|{"user_id": 24, "calories_burnt": 250.6999969482422, "num_steps": 5014, "miles_walked": 2.506999969482422, "time_stamp": "2018-07-22 06:44:25.732267", "device_id": 5}   |
|{"user_id": 24, "calories_burnt": 126.80000305175781, "num_steps": 2536, "miles_walked": 1.2680000066757202, "time_stamp": "2018-07-21 01:18:10.732306", "device_id": 13}|
|{"user_id": 4, "calories_burnt": 365.70001220703125, "num_steps": 7314, "miles_walked": 3.6570000648498535, "time_stamp": "2018-07-24 12:42


Following code snippet demonstrates the process of extracting data from JSON values in a Spark DataFrame and performing some data transformations.

- We first define a schema for the JSON data using `StructType` and `StructField`.
- Then, we use the `from_json` function to extract JSON values into separate columns based on the defined schema.
- We select relevant columns from the extracted JSON data.
- Additionally, we perform additional transformations:
  - Extracting the date and time from a timestamp column using `to_date` and `date_format`.
- Finally, we select the desired columns and drop the JSON object column.

This code prepares the data for further analysis or visualization, ensuring it's in a structured format suitable for downstream processing.


In [ ]:
from pyspark.sql.functions import col, to_date, date_format, hour, minute, second,  from_json
from pyspark.sql.types import StructType, StructField, StringType, IntegerType, FloatType, TimestampType

# Define schema for JSON data
schema = StructType([
    StructField("user_id", IntegerType()),
    StructField("calories_burnt", FloatType()),
    StructField("num_steps", IntegerType()),
    StructField("miles_walked", FloatType()),
    StructField("time_stamp", TimestampType()),
    StructField("device_id", IntegerType())
])

# Extract JSON values into separate columns and select other columns
deviceData_json = deviceData_raw.select(
    from_json(col("value"), schema).alias("json_data")
).selectExpr(
    "json_data.*"
)

# Show DataFrame
deviceData_json.show(truncate=False)

deviceData_raw = deviceData_raw.withColumn("date", to_date(col("timestamp")))  # Extract date
deviceData_raw = deviceData_raw.withColumn("time", date_format(col("timestamp"), "HH:mm:ss"))  # Extract time

#json object shows simmilar data hence we can drop it 

deviceData = deviceData_raw.select(
    'device_id',
    'user_id',
    'id',
    'miles_walked',
    'num_steps',
    'calories_burnt',
    'date',
    'time')


+-------+--------------+---------+------------+--------------------------+---------+
|user_id|calories_burnt|num_steps|miles_walked|time_stamp                |device_id|
+-------+--------------+---------+------------+--------------------------+---------+
|24     |250.7         |5014     |2.507       |2018-07-22 06:44:25.732267|5        |
|24     |126.8         |2536     |1.268       |2018-07-21 01:18:10.732306|13       |
|4      |365.7         |7314     |3.657       |2018-07-24 12:42:53.732332|5        |
|22     |489.8         |9796     |4.898       |2018-07-23 22:56:23.732358|10       |
|34     |280.15        |5603     |2.8015      |2018-07-21 13:50:39.732385|13       |
|21     |591.6         |11832    |5.916       |2018-07-23 11:05:48.732412|1        |
|7      |548.1         |10962    |5.481       |2018-07-23 02:10:39.732438|12       |
|33     |272.4         |5448     |2.724       |2018-07-22 17:42:18.732465|4        |
|16     |381.85        |7637     |3.8185      |2018-07-21 12:21:2

The following code creates a temporary view named `deviceData` in Spark SQL for further analysis:


In [ ]:
deviceData.createOrReplaceTempView('deviceData')

In [ ]:
%sql
SELECT * FROM deviceData

device_id user_id id miles_walked num_steps calories_burnt date time 5 24 950000 2.507 5014 250.7 2018-07-22 06:44:25 13 24 950001 1.268 2536 126.8 2018-07-21 01:18:10 5 4 950002 3.657 7314 365.7 2018-07-24 12:42:53 10 22 950003 4.898 9796 489.8 2018-07-23 22:56:23 13 34 950004 2.8015 5603 280.15 2018-07-21 13:50:39 1 21 950005 5.916 11832 591.6 2018-07-23 11:05:48 12 7 950006 5.481 10962 548.1 2018-07-23 02:10:39 4 33 950007 2.724 5448 272.4 2018-07-22 17:42:18 5 16 950008 3.8185 7637 381.85 2018-07-21 12:21:21 8 27 950009 5.8545 11709 585.44995 2018-07-22 12:40:55 12 36 950010 1.442 2884 144.2 2018-07-24 01:37:42 19 10 950011 0.659 1318 65.9 2018-07-22 00:06:53 4 23 950012 3.8195 7639 381.95 2018-07-23 02:07:55 9 19 950013 4.4225 8845 442.25 2018-07-23 04:23:33 17 36 950014 0.94 1880 94.0 2018-07-21 19:24:03 13 24 950015 0.7885 1577 78.85 2018-07-23 02:51:40 10 23 950016 1.014 2028 101.40001 2018-07-22 00:30:38 17 22 950017 3.5215 7043 352.15002 2018-07-23 17:35:09 7 32 950018 2.5405 5081 254.04999 2018-07-21 21:51:39 13 33 950019 5.1615 10323 516.15 2018-07-21 16:05:05 15 15 950020 4.522 9044 452.19998 2018-07-24 04:42:23 16 16 950021 2.774 5548 277.4 2018-07-23 20:27:00 16 35 950022 2.3755 4751 237.55 2018-07-21 05:55:18 11 9 950023 1.0745 2149 107.45 2018-07-21 18:02:59 12 8 950024 1.7895 3579 178.95 2018-07-23 14:31:14 9 35 950025 5.2595 10519 525.95 2018-07-23 06:08:55 7 18 950026 3.766 7532 376.6 2018-07-22 19:28:17 2 35 950027 4.342 8684 434.2 2018-07-23 13:25:23 9 13 950028 2.8875 5775 288.75 2018-07-23 16:01:06 9 26 950029 1.0605 2121 106.05 2018-07-21 15:28:56 14 33 950030 4.9235 9847 492.35 2018-07-20 07:29:57 11 1 950031 1.9415 3883 194.15 2018-07-23 10:08:20 18 31 950032 3.929 7858 392.9 2018-07-21 14:07:56 17 9 950033 1.2625 2525 126.25001 2018-07-23 10:57:02 13 31 950034 4.136 8272 413.6 2018-07-20 08:22:51 2 30 950035 3.321 6642 332.1 2018-07-22 07:22:51 15 34 950036 1.658 3316 165.8 2018-07-24 17:33:50 20 29 950037 5.211 10422 521.1 2018-07-22 05:42:54 18 24 950038 3.1025 6205 310.25 2018-07-20 08:19:38 15 11 950039 1.524 3048 152.40001 2018-07-24 07:34:25 19 4 950040 1.76 3520 176.0 2018-07-23 13:22:37 10 23 950041 3.3285 6657 332.85 2018-07-22 02:45:44 7 11 950042 3.2925 6585 329.25 2018-07-20 18:26:30 14 6 950043 2.4255 4851 242.54999 2018-07-22 23:42:47 12 29 950044 5.6915 11383 569.15 2018-07-23 16:02:00 15 38 950045 3.521 7042 352.09998 2018-07-24 13:25:22 14 10 950046 5.042 10084 504.19998 2018-07-22 07:06:15 13 10 950047 3.108 6216 310.80002 2018-07-20 17:43:52 8 7 950048 2.9615 5923 296.15 2018-07-23 20:44:21 13 19 950049 1.0715 2143 107.149994 2018-07-20 23:11:26 14 21 950050 2.466 4932 246.6 2018-07-22 03:52:07 5 30 950051 1.0385 2077 103.85 2018-07-21 03:43:10 7 33 950052 1.8195 3639 181.95 2018-07-23 09:25:46 10 36 950053 2.509 5018 250.90001 2018-07-21 12:14:38 3 9 950054 2.961 5922 296.1 2018-07-20 20:19:30 17 5 950055 3.6025 7205 360.25 2018-07-22 06:13:06 16 22 950056 5.536 11072 553.6 2018-07-22 23:55:36 4 6 950057 1.2315 2463 123.15 2018-07-21 11:54:13 9 9 950058 4.468 8936 446.8 2018-07-21 06:50:28 14 27 950059 5.9075 11815 590.75 2018-07-20 20:05:32 8 20 950060 5.672 11344 567.2 2018-07-22 10:13:18 5 29 950061 1.3635 2727 136.35 2018-07-24 11:48:08 16 1 950062 3.477 6954 347.7 2018-07-23 07:09:43 16 30 950063 1.986 3972 198.59999 2018-07-21 04:29:53 5 33 950064 2.545 5090 254.5 2018-07-23 19:49:50 17 31 950065 4.932 9864 493.2 2018-07-23 00:18:59 16 15 950066 1.0295 2059 102.95 2018-07-21 20:36:05 6 33 950067 5.779 11558 577.89996 2018-07-20 04:32:14 14 11 950068 4.003 8006 400.3 2018-07-20 10:58:15 3 8 950069 5.191 10382 519.1 2018-07-21 01:13:26 16 30 950070 1.3455 2691 134.55 2018-07-20 12:32:01 2 12 950071 3.4575 6915 345.75 2018-07-23 13:11:48 7 22 950072 1.1035 2207 110.35 2018-07-23 12:16:38 8 6 950073 5.851 11702 585.1 2018-07-20 08:57:01 12 23 950074 3.1125 6225 311.25 2018-07-21 01:10:07 7 12 950075 2.8335 5667 283.34998 2018-07-21 10:11:29 9 10 950076 0.916 1832 91.6 2018-07-2

CREATING BRONZE DELTA TABLE FOR deviceData

In [ ]:
%sql
CREATE TABLE bronze_device 
USING DELTA
COMMENT 'Bronze table in the architecture'
TBLPROPERTIES ('type'='bronze')
AS 
SELECT * FROM deviceData;


num_affected_rows num_inserted_rows

The following code uses the `%fs ls` magic command to list files and directories in the specified directory within Databricks File System (DBFS):



In [ ]:
%fs ls dbfs:/databricks-datasets/iot-stream/data-user

path name size modificationTime dbfs:/databricks-datasets/iot-stream/data-user/userData.csv userData.csv 1374 1532465793000


The following code snippet reads data from a CSV file into a DataFrame named `userData` using Apache Spark:



In [ ]:
userData = spark.read.format('csv')\
    .option('header' , True)\
    .option('inferSchema' , True) \
    .load('dbfs:/databricks-datasets/iot-stream/data-user')

In [ ]:
userData.show()

+------+------+---+------+------+------+-------------+-----------+------+----+
|userid|gender|age|height|weight|smoker|familyhistory|cholestlevs|    bp|risk|
+------+------+---+------+------+------+-------------+-----------+------+----+
|     1|     F| 40|    63|   100|     N|            Y|       High|  High|   5|
|     2|     M| 34|    69|   150|     N|            Y|     Normal|Normal| -10|
|     3|     F| 35|    60|   134|     N|            N|     Normal|Normal| -10|
|     4|     F| 38|    59|   131|     Y|            Y|       High|  High|  20|
|     5|     F| 29|    59|   102|     N|            N|       High|Normal|  10|
|     6|     M| 37|    73|   174|     Y|            N|       High|  High|  20|
|     7|     M| 25|    72|   171|     Y|            N|       High|  High|  20|
|     8|     M| 26|    75|   166|     N|            Y|       High|Normal|  10|
|     9|     F| 36|    64|   115|     N|            N|     Normal|Normal| -10|
|    10|     F| 39|    65|   123|     Y|            

In [ ]:
userData.printSchema()                  

root
 |-- userid: integer (nullable = true)
 |-- gender: string (nullable = true)
 |-- age: integer (nullable = true)
 |-- height: integer (nullable = true)
 |-- weight: integer (nullable = true)
 |-- smoker: string (nullable = true)
 |-- familyhistory: string (nullable = true)
 |-- cholestlevs: string (nullable = true)
 |-- bp: string (nullable = true)
 |-- risk: integer (nullable = true)




 
The following code creates a temporary view named `userData` in Spark SQL for further analysis:



In [ ]:
userData.createOrReplaceTempView('userData')

In [ ]:
%sql
SELECT * 
FROM userData 

userid gender age height weight smoker familyhistory cholestlevs bp risk 1 F 40 63 100 N Y High High 5 2 M 34 69 150 N Y Normal Normal -10 3 F 35 60 134 N N Normal Normal -10 4 F 38 59 131 Y Y High High 20 5 F 29 59 102 N N High Normal 10 6 M 37 73 174 Y N High High 20 7 M 25 72 171 Y N High High 20 8 M 26 75 166 N Y High Normal 10 9 F 36 64 115 N N Normal Normal -10 10 F 39 65 123 Y N Normal Normal 20 11 F 28 62 135 N Y Normal Normal -10 12 M 29 72 149 N N High Normal 10 13 F 29 58 105 Y N Normal Normal 20 14 M 26 69 135 Y N Normal Normal 20 15 F 34 59 113 N N Normal High 0 16 M 40 66 165 N Y Normal Normal -10 17 F 38 58 131 Y N Normal Normal 20 18 F 32 59 116 N N Normal Normal -10 19 F 32 65 114 N N Normal Normal -10 20 F 28 62 127 Y N Normal High 20 21 M 25 65 152 N N Normal Normal -10 22 F 26 64 105 N N Normal Normal -10 23 F 34 62 109 N N Normal Normal -10 24 F 30 61 109 N N High Normal 10 25 F 39 60 153 N N Normal Normal -10 26 M 38 71 178 N Y High High 5 27 M 42 73 178 Y Y High High 20 28 M 42 75 189 Y Y High High 20 29 M 35 73 195 N N High High 5 30 F 35 63 159 Y N Normal High 20 31 M 34 75 196 Y Y Normal Normal 20 32 F 41 59 140 N Y High Normal 10 33 F 60 59 147 N Y High High 5 34 F 45 65 167 N Y Normal High 5 35 M 58 64 179 N Y Normal High 5 36 M 52 67 173 N Y High High 5 37 M 51 75 191 N Y High Normal 10 38 M 59 70 196 N Y Normal Normal -10

CREATING BRONZE DELTA TABLE FOR deviceData

In [ ]:
%sql
CREATE TABLE bronze_user 
USING DELTA
COMMENT 'Bronze table in the architecture'
TBLPROPERTIES ('type'='bronze')
AS 
SELECT * FROM userData;


num_affected_rows num_inserted_rows

**Data Ingestion and Transformation**

Data has been successfully ingested into the notebook. We've performed initial data quality checks and proceeded with the transformation process. Here's a summary of the steps taken so far:

1. **Ingestion:** Data has been ingested from the source, and initial exploration has been conducted to ensure successful ingestion.

2. **Data Quality Checks:** We've conducted preliminary data quality checks to identify any anomalies or inconsistencies in the dataset.

3. **Timestamp Column Transformation:** The timestamp column has been broken down into separate columns for date and time using PySpark DataFrames, facilitating easier analysis and manipulation.

4. **View Creation:** Views have been created out of selected columns, allowing for seamless integration of DataFrame operations with SQL queries. This marks the transition from the raw to the bronze layer of the data processing pipeline.

Next, we will proceed with maintaining aggregation at the hourly level in the bronze to silver layer, enabling more granular analysis and visualization of the data.

This Markdown cell provides a structured overview of the data processing steps performed, enhancing documentation and readability within the notebook.



<h2> Bronze to Silver </h2>

In [ ]:
%sql
SHOW tables

database tableName isTemporary default bronze_device false default bronze_user false devicedata true userdata true

In [ ]:
%sql
SELECT count(*) from bronze_device

count(1) 1000000

This SQL snippet first checks if a view named `agg_deviceData` exists and drops it if present. Then, it creates a new temporary view `agg_deviceData`, aggregating data from the `deviceData` DataFrame. The aggregation includes rounding the sum of miles walked, step count, and calories burnt to two decimal places, grouped by device ID, user ID, date, and hour extracted from the timestamp. This aggregation enhances data granularity for analysis. The view creation signifies the transition from the bronze to the silver layer of the data processing pipeline, facilitating further analysis and visualization at an hourly level.

In [ ]:
%sql
DROP view IF EXISTS agg_deviceData;

CREATE temp view agg_deviceData AS (
SELECT
    device_id,
    user_id,
    ROUND(SUM(miles_walked), 2) AS miles_walked,
    ROUND(SUM(num_steps), 2) AS step_count,
    ROUND(SUM(calories_burnt), 2) AS calories_count,
    date,
    HOUR(time) AS hour
FROM 
    bronze_device
GROUP BY 
    device_id, user_id, date, HOUR(time)
)

In [ ]:
%sql
SELECT count(*) as after_aggregation FROM agg_deviceData

after_aggregation 92342

In [ ]:
%sql
SELECT * from agg_deviceData

device_id user_id miles_walked step_count calories_count date hour 9 32 18.3 36606 1830.3 2018-07-20 10 6 26 79.01 158024 7901.2 2018-07-21 18 14 23 32.39 64783 3239.15 2018-07-23 22 2 26 43.97 87940 4397.0 2018-07-23 2 10 29 54.0 108006 5400.3 2018-07-22 19 14 8 12.92 25831 1291.55 2018-07-20 5 11 13 53.6 107209 5360.45 2018-07-24 13 9 7 49.48 98961 4948.05 2018-07-20 11 1 4 25.06 50120 2506.0 2018-07-20 14 2 31 29.12 58247 2912.35 2018-07-20 16 13 16 69.92 139830 6991.5 2018-07-24 6 8 23 34.04 68087 3404.35 2018-07-22 19 19 28 46.0 91991 4599.55 2018-07-22 0 11 30 13.74 27486 1374.3 2018-07-19 18 6 36 35.3 70605 3530.25 2018-07-21 21 19 4 15.0 30008 1500.4 2018-07-21 4 8 3 60.88 121750 6087.5 2018-07-21 6 16 17 62.77 125543 6277.15 2018-07-24 4 10 21 54.86 109725 5486.25 2018-07-24 6 15 25 54.88 109757 5487.85 2018-07-21 22 20 3 33.35 66708 3335.4 2018-07-24 18 20 28 66.04 132080 6604.0 2018-07-24 15 15 5 59.42 118839 5941.95 2018-07-23 9 5 21 9.19 18371 918.55 2018-07-20 3 7 20 15.81 31613 1580.65 2018-07-24 2 13 1 38.22 76431 3821.55 2018-07-22 4 14 7 69.28 138564 6928.2 2018-07-23 17 7 11 26.88 53750 2687.5 2018-07-20 17 7 22 24.91 49811 2490.55 2018-07-23 10 19 24 26.57 53132 2656.6 2018-07-19 21 6 34 57.08 114166 5708.3 2018-07-22 20 13 2 45.18 90353 4517.65 2018-07-23 11 15 33 34.08 68160 3408.0 2018-07-23 8 16 27 11.58 23158 1157.9 2018-07-22 9 14 35 27.12 54234 2711.7 2018-07-22 23 19 34 53.04 106086 5304.3 2018-07-24 0 10 4 54.42 108843 5442.15 2018-07-23 4 3 23 22.84 45680 2284.0 2018-07-24 11 14 29 31.98 63953 3197.65 2018-07-20 8 14 20 57.89 115779 5788.95 2018-07-23 17 12 11 47.85 95692 4784.6 2018-07-22 19 8 11 49.67 99337 4966.85 2018-07-24 15 12 5 96.5 192992 9649.6 2018-07-20 2 10 14 37.86 75713 3785.65 2018-07-20 5 8 16 84.83 169667 8483.35 2018-07-20 19 12 26 44.26 88513 4425.65 2018-07-22 9 1 29 46.09 92187 4609.35 2018-07-20 6 20 31 26.81 53613 2680.65 2018-07-21 5 12 34 47.09 94172 4708.6 2018-07-23 16 9 16 105.58 211160 10558.0 2018-07-22 20 20 38 23.2 46404 2320.2 2018-07-23 2 12 7 62.01 124012 6200.6 2018-07-23 7 6 34 46.84 93671 4683.55 2018-07-20 16 13 18 22.77 45549 2277.45 2018-07-23 17 13 8 63.44 126885 6344.25 2018-07-23 3 6 6 45.76 91513 4575.65 2018-07-23 2 2 16 58.48 116961 5848.05 2018-07-21 11 13 27 26.54 53081 2654.05 2018-07-22 18 3 24 14.61 29228 1461.4 2018-07-24 19 19 21 37.36 74724 3736.2 2018-07-19 20 2 10 55.96 111917 5595.85 2018-07-23 2 20 21 92.88 185768 9288.4 2018-07-24 10 3 16 32.8 65591 3279.55 2018-07-23 3 1 34 27.1 54195 2709.75 2018-07-23 8 9 15 66.7 133409 6670.45 2018-07-21 10 12 29 56.36 112727 5636.35 2018-07-22 18 19 5 70.16 140314 7015.7 2018-07-20 15 10 38 58.4 116808 5840.4 2018-07-21 18 3 5 29.06 58114 2905.7 2018-07-24 4 10 11 57.77 115535 5776.75 2018-07-24 8 2 27 65.44 130881 6544.05 2018-07-21 1 15 16 10.8 21608 1080.4 2018-07-24 19 16 15 34.35 68698 3434.9 2018-07-23 12 20 14 35.92 71837 3591.85 2018-07-21 22 10 8 40.54 81077 4053.85 2018-07-21 3 12 15 24.75 49502 2475.1 2018-07-24 6 12 8 64.16 128315 6415.75 2018-07-20 20 6 23 53.73 107455 5372.75 2018-07-21 11 13 36 49.6 99204 4960.2 2018-07-23 9 5 26 21.26 42514 2125.7 2018-07-21 0 14 14 50.3 100595 5029.75 2018-07-23 11 17 33 56.87 113740 5687.0 2018-07-24 13 17 6 38.08 76156 3807.8 2018-07-22 20 17 22 74.28 148552 7427.6 2018-07-20 23 17 29 33.98 67951 3397.55 2018-07-20 7 6 31 73.67 147349 7367.45 2018-07-23 2 13 21 28.69 57379 2868.95 2018-07-24 13 17 24 51.97 103937 5196.85 2018-07-22 2 20 34 53.08 106158 5307.9 2018-07-21 4 8 14 56.26 112515 5625.75 2018-07-23 4 17 35 51.1 102192 5109.6 2018-07-21 15 17 36 49.91 99817 4990.85 2018-07-24 9 2 24 38.64 77286 3864.3 2018-07-20 5 13 7 76.73 153462 7673.1 2018-07-23 4 15 34 41.6 83204 4160.2 2018-07-24 11 18 12 9.84 19685 984.25 2018-07-23 21 14 28 43.66 87321 4366.05 2018-07-20 0 6 29 85.79 171589 8579.45 2018-07-22 21 18 24 41.55 83104 4155.2 2018-07-24 10 15 16 35.32 70637 3531.85 2018-07-23 21 16 2 45.94 91886 4594.3 2018-07-20 18 9 28 30.3 60604 3030

CREATING SILVER DELTA TABLE FOR deviceData

In [ ]:
%sql
CREATE TABLE silver_device
USING DELTA
COMMENT 'Silver table in the architecture'
TBLPROPERTIES ('type'='silver')
AS 
SELECT * FROM agg_deviceData;

num_affected_rows num_inserted_rows

Following SQL command performs the following processing steps:
- It calculates the BMI for each record in the `userdata` table by applying the formula (weight / height^2) * 703.
- It categorizes the BMI values into different categories ('Underweight', 'Normal Weight', 'Overweight', 'Obese') based on standard BMI ranges.
- The resulting dataset is stored in a temporary view named `calc_user`.

This view creation enables seamless integration of BMI calculations and categorizations into subsequent data analysis tasks. By categorizing BMI, it provides valuable insights into individuals' health status, aiding in personalized health assessments and interventions. Additionally, the use of temporary views ensures that the processing is efficient and does not persist beyond the current session, maintaining data integrity and reducing storage overhead. Overall, this SQL code enhances the functionality and analytical capabilities of the `userdata` dataset within the Databricks environment, empowering users to derive actionable insights for health-related decision-making.


In [ ]:


%sql
DROP view if exists calc_user;

CREATE TEMP VIEW calc_user AS
(
-- Calculate BMI and categorize
SELECT *,
ROUND(((weight / height / height) * 703), 2) AS BMI,
CASE 
    WHEN ((weight / height / height) * 703) < 18.5 THEN 'Underweight'
    WHEN ((weight / height / height) * 703) >= 18.5 AND ((weight / height / height) * 703) < 24.9 THEN 'Normal Weight'
    WHEN ((weight / height / height) * 703) >= 24.9 AND ((weight / height / height) * 703) < 29.9 THEN 'Overweight'
    ELSE 'Obese'
END AS BMI_Category
FROM bronze_user
)


CREATING SILVER DELTA TABLE FOR userData

In [ ]:
%sql
CREATE TABLE silver_user
USING DELTA
COMMENT 'Silver table in the architecture'
TBLPROPERTIES ('type'='silver')
AS 
SELECT * FROM calc_user;

num_affected_rows num_inserted_rows

In [ ]:
%sql
SELECT date, count(date) from silver_device
GROUP BY date;

date count(date) 2018-07-20 18193 2018-07-24 15132 2018-07-22 18167 2018-07-23 18182 2018-07-21 18186 2018-07-19 4482

We're removing the data from July 19, 2018, because it's incomplete and not useful. After that, we'll make all the rest of the user data available for consumption


CREATING GOLD DELTA TABLE FOR deviceData for consumption and visualization


In [ ]:
%sql
CREATE TABLE gold_device
USING DELTA
COMMENT 'Gold table in the architecture'
TBLPROPERTIES ('type'='gold')
AS 
SELECT * FROM silver_device
where date != '2018-07-19';

num_affected_rows num_inserted_rows

CREATING GOLD DELTA TABLE FOR userData for consumption and visualization

In [ ]:
%sql
CREATE TABLE gold_user
USING DELTA
COMMENT 'Gold table in the architecture'
TBLPROPERTIES ('type'='gold')
AS 
SELECT * FROM silver_user;

num_affected_rows num_inserted_rows

In [ ]:
%sql
SHOW tables;

database tableName isTemporary default bronze_device false default bronze_user false default gold_device false default gold_user false default silver_device false default silver_user false agg_devicedata true calc_user true devicedata true userdata true

In [ ]:
#%fs rm -r dbfs:/user/hive/warehouse 